In [37]:
import config

In [38]:
import spotipy
import json
import pandas as pd
from spotipy.oauth2 import SpotifyClientCredentials

In [39]:
from typing import List, Dict

In [40]:
sp = spotipy.Spotify(auth_manager=SpotifyClientCredentials(client_id= config.client_id,
                                                           client_secret= config.client_secret))

In [15]:
playlist0 = sp.user_playlist_tracks("spotify", "4oA5fkQGa2rI7tmGJGT7GT",market="GB")
playlist0 # Using the base playlist called 'The Long Playlist' with 4871 songs.

{'href': 'https://api.spotify.com/v1/playlists/4oA5fkQGa2rI7tmGJGT7GT/tracks?offset=0&limit=100&market=GB&additional_types=track',
 'items': [{'added_at': '2018-02-05T04:37:10Z',
   'added_by': {'external_urls': {'spotify': 'https://open.spotify.com/user/zlukee'},
    'href': 'https://api.spotify.com/v1/users/zlukee',
    'id': 'zlukee',
    'type': 'user',
    'uri': 'spotify:user:zlukee'},
   'is_local': False,
   'primary_color': None,
   'track': {'album': {'album_type': 'album',
     'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/04gDigrS5kc9YWfZHwBETP'},
       'href': 'https://api.spotify.com/v1/artists/04gDigrS5kc9YWfZHwBETP',
       'id': '04gDigrS5kc9YWfZHwBETP',
       'name': 'Maroon 5',
       'type': 'artist',
       'uri': 'spotify:artist:04gDigrS5kc9YWfZHwBETP'}],
     'external_urls': {'spotify': 'https://open.spotify.com/album/5zClcGCSWj926AMjvBNSLc'},
     'href': 'https://api.spotify.com/v1/albums/5zClcGCSWj926AMjvBNSLc',
     'id': '5zCl

In [16]:
playlist0['items'][0] #checking the values for the first song.

{'added_at': '2018-02-05T04:37:10Z',
 'added_by': {'external_urls': {'spotify': 'https://open.spotify.com/user/zlukee'},
  'href': 'https://api.spotify.com/v1/users/zlukee',
  'id': 'zlukee',
  'type': 'user',
  'uri': 'spotify:user:zlukee'},
 'is_local': False,
 'primary_color': None,
 'track': {'album': {'album_type': 'album',
   'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/04gDigrS5kc9YWfZHwBETP'},
     'href': 'https://api.spotify.com/v1/artists/04gDigrS5kc9YWfZHwBETP',
     'id': '04gDigrS5kc9YWfZHwBETP',
     'name': 'Maroon 5',
     'type': 'artist',
     'uri': 'spotify:artist:04gDigrS5kc9YWfZHwBETP'}],
   'external_urls': {'spotify': 'https://open.spotify.com/album/5zClcGCSWj926AMjvBNSLc'},
   'href': 'https://api.spotify.com/v1/albums/5zClcGCSWj926AMjvBNSLc',
   'id': '5zClcGCSWj926AMjvBNSLc',
   'images': [{'height': 640,
     'url': 'https://i.scdn.co/image/ab67616d0000b27392f2d790c6a97b195f66d51e',
     'width': 640},
    {'height': 300,
     

In [17]:
song = playlist0['items'][0]['track']['id'] #extracting the song id.
song

'6ECp64rv50XVz93WvxXMGF'

In [18]:
sp.audio_features(song)#Checking the features of any one song.

[{'danceability': 0.712,
  'energy': 0.862,
  'key': 5,
  'loudness': -4.612,
  'mode': 0,
  'speechiness': 0.0378,
  'acousticness': 0.0525,
  'instrumentalness': 0,
  'liveness': 0.093,
  'valence': 0.809,
  'tempo': 95.051,
  'type': 'audio_features',
  'id': '6ECp64rv50XVz93WvxXMGF',
  'uri': 'spotify:track:6ECp64rv50XVz93WvxXMGF',
  'track_href': 'https://api.spotify.com/v1/tracks/6ECp64rv50XVz93WvxXMGF',
  'analysis_url': 'https://api.spotify.com/v1/audio-analysis/6ECp64rv50XVz93WvxXMGF',
  'duration_ms': 206200,
  'time_signature': 4}]

#### Building df of feature values of all the songs in the playlist

In [9]:
def get_playlist_tracks(username, playlist_id):
    results = sp.user_playlist_tracks(username,playlist_id,market="GB")
    tracks = results['items']
    while results['next']:
        results = sp.next(results)
        tracks.extend(results['items'])
    return tracks

In [10]:
tracks=get_playlist_tracks("spotify", "4oA5fkQGa2rI7tmGJGT7GT")

In [11]:
import pprint
pprint.pprint(tracks[0])


{'added_at': '2018-02-05T04:37:10Z',
 'added_by': {'external_urls': {'spotify': 'https://open.spotify.com/user/zlukee'},
              'href': 'https://api.spotify.com/v1/users/zlukee',
              'id': 'zlukee',
              'type': 'user',
              'uri': 'spotify:user:zlukee'},
 'is_local': False,
 'primary_color': None,
 'track': {'album': {'album_type': 'album',
                     'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/04gDigrS5kc9YWfZHwBETP'},
                                  'href': 'https://api.spotify.com/v1/artists/04gDigrS5kc9YWfZHwBETP',
                                  'id': '04gDigrS5kc9YWfZHwBETP',
                                  'name': 'Maroon 5',
                                  'type': 'artist',
                                  'uri': 'spotify:artist:04gDigrS5kc9YWfZHwBETP'}],
                     'external_urls': {'spotify': 'https://open.spotify.com/album/5zClcGCSWj926AMjvBNSLc'},
                     'href': 'ht

In [60]:
def extract_features(songs):
    list_of_audio_features = []
    for item in songs:
        try:
            list_of_audio_features.append(sp.audio_features(item['track']['id'])[0])
        except: 
            continue
    return list_of_audio_features

In [61]:
features = extract_features(tracks)

NameError: name 'tracks' is not defined

In [92]:
features

[{'danceability': 0.712, 'energy': 0.862, 'key': 5, 'loudness': -4.612, 'mode': 0, 'speechiness': 0.0378, 'acousticness': 0.0525, 'instrumentalness': 0, 'liveness': 0.093, 'valence': 0.809, 'tempo': 95.051, 'type': 'audio_features', 'id': '6ECp64rv50XVz93WvxXMGF', 'uri': 'spotify:track:6ECp64rv50XVz93WvxXMGF', 'track_href': 'https://api.spotify.com/v1/tracks/6ECp64rv50XVz93WvxXMGF', 'analysis_url': 'https://api.spotify.com/v1/audio-analysis/6ECp64rv50XVz93WvxXMGF', 'duration_ms': 206200, 'time_signature': 4}, {'danceability': 0.692, 'energy': 0.394, 'key': 11, 'loudness': -8.745, 'mode': 0, 'speechiness': 0.207, 'acousticness': 0.472, 'instrumentalness': 0.000191, 'liveness': 0.117, 'valence': 0.324, 'tempo': 89.936, 'type': 'audio_features', 'id': '1RGasjWLZ4qMN7wbtkLa3u', 'uri': 'spotify:track:1RGasjWLZ4qMN7wbtkLa3u', 'track_href': 'https://api.spotify.com/v1/tracks/1RGasjWLZ4qMN7wbtkLa3u', 'analysis_url': 'https://api.spotify.com/v1/audio-analysis/1RGasjWLZ4qMN7wbtkLa3u', 'duration_

In [59]:
tracks_df=pd.DataFrame(features)    
tracks_df=tracks_df[["danceability","energy","loudness","speechiness","acousticness",
    "instrumentalness","liveness","valence","tempo","id","duration_ms"]]

tracks_df

NameError: name 'features' is not defined

In [13]:
categories = sp.categories(country='GB',locale='en')

In [14]:
pprint.pprint(categories)

{'categories': {'href': 'https://api.spotify.com/v1/browse/categories?country=GB&locale=en&offset=0&limit=20',
                'items': [{'href': 'https://api.spotify.com/v1/browse/categories/toplists',
                           'icons': [{'height': 275,
                                      'url': 'https://t.scdn.co/media/derived/toplists_11160599e6a04ac5d6f2757f5511778f_0_0_275_275.jpg',
                                      'width': 275}],
                           'id': 'toplists',
                           'name': 'Top Lists'},
                          {'href': 'https://api.spotify.com/v1/browse/categories/0JQ5DAqbMKFLVaM30PMBm4',
                           'icons': [{'height': None,
                                      'url': 'https://t.scdn.co/images/8e508d7eb5b843a89c368c9507ecc429.jpeg',
                                      'width': None}],
                           'id': '0JQ5DAqbMKFLVaM30PMBm4',
                           'name': 'Summer'},
                          {

In [15]:
category_id = categories['categories']['items'][2]['id']
category_id

'0JQ5DAqbMKFEC4WFtoNRpw'

In [16]:
def get_category_ids():
    categories = sp.categories(country='GB',locale='en',limit=50)
    category_ids = []
    for item in categories['categories']['items']:
        category_ids.append(item['id'])
    return category_ids

In [17]:
category_ids = get_category_ids()

In [18]:
len(category_ids)

50

In [19]:
category_playlists = sp.category_playlists(category_id = category_id, country = 'GB')

In [20]:
pprint.pprint(category_playlists)

{'playlists': {'href': 'https://api.spotify.com/v1/browse/categories/0JQ5DAqbMKFEC4WFtoNRpw/playlists?country=GB&offset=0&limit=20',
               'items': [{'collaborative': False,
                          'description': "The UK's biggest playlist. Cover: "
                                         'Clavish & D-Block Europe',
                          'external_urls': {'spotify': 'https://open.spotify.com/playlist/37i9dQZF1DWY4lFlS4Pnso'},
                          'href': 'https://api.spotify.com/v1/playlists/37i9dQZF1DWY4lFlS4Pnso',
                          'id': '37i9dQZF1DWY4lFlS4Pnso',
                          'images': [{'height': None,
                                      'url': 'https://i.scdn.co/image/ab67706f00000003b334c6ce53efdd96c20d4aaa',
                                      'width': None}],
                          'name': 'Hot Hits UK',
                          'owner': {'display_name': 'Spotify',
                                    'external_urls': {'spotify': 

In [21]:
playlist_id = category_playlists['playlists']['items'][0]['id']

In [22]:
playlist_id

'37i9dQZF1DWY4lFlS4Pnso'

In [23]:
pprint.pprint(category_playlists['playlists']['items'])

[{'collaborative': False,
  'description': "The UK's biggest playlist. Cover: Clavish & D-Block Europe",
  'external_urls': {'spotify': 'https://open.spotify.com/playlist/37i9dQZF1DWY4lFlS4Pnso'},
  'href': 'https://api.spotify.com/v1/playlists/37i9dQZF1DWY4lFlS4Pnso',
  'id': '37i9dQZF1DWY4lFlS4Pnso',
  'images': [{'height': None,
              'url': 'https://i.scdn.co/image/ab67706f00000003b334c6ce53efdd96c20d4aaa',
              'width': None}],
  'name': 'Hot Hits UK',
  'owner': {'display_name': 'Spotify',
            'external_urls': {'spotify': 'https://open.spotify.com/user/spotify'},
            'href': 'https://api.spotify.com/v1/users/spotify',
            'id': 'spotify',
            'type': 'user',
            'uri': 'spotify:user:spotify'},
  'primary_color': None,
  'public': None,
  'snapshot_id': 'MTY2OTMzNDQwMCwwMDAwMDAwMDFmZmMyMmVlNWNlMjUwYzY1ZTQ4YTdkZWFjNTQwOTMx',
  'tracks': {'href': 'https://api.spotify.com/v1/playlists/37i9dQZF1DWY4lFlS4Pnso/tracks',
           

In [24]:
def get_category_playlists(category_ids):
    x = []
    for i in category_ids:
        category_playlists = sp.category_playlists(category_id = i, country = 'GB', limit=50)
        for item in category_playlists['playlists']['items']:
            try: 
                x.append(item['id'])
            except:
                continue
    return x

In [25]:
playlist_ids = get_category_playlists(category_ids)

In [26]:
playlist_ids

['37i9dQZF1DWY4lFlS4Pnso',
 '37i9dQZF1DX5uokaTN4FTR',
 '37i9dQZF1DXcBWIGoYBM5M',
 '37i9dQZF1DX4W3aJJYCDfV',
 '37i9dQZF1DX0XUsuxWHRQd',
 '37i9dQZF1DWSOkubnsDCSS',
 '37i9dQZF1DX4SBhb3fqCJd',
 '37i9dQZF1DX4dyzvuaRJ0n',
 '37i9dQZF1DXcF6B6QPhFDv',
 '37i9dQZF1DX1lVhptIYRda',
 '37i9dQZEVXbLnolsZ8PSNw',
 '37i9dQZEVXbMDoHDwVN2tF',
 '37i9dQZEVXbLiRSasKsNU9',
 '37i9dQZEVXbL3DLHfQeDmV',
 '37i9dQZF1DWWevrQ6HpxHI',
 '37i9dQZF1DWVrBRunTOXCY',
 '37i9dQZF1DX3ITTpGLyrci',
 '37i9dQZF1DWW5hMh7LGtmv',
 '37i9dQZF1DX5h2VnNTubsH',
 '37i9dQZF1DX1JBJX3hwjvu',
 '37i9dQZF1DWZqbnP2e1SEM',
 '37i9dQZF1DWSwyaV6GLT48',
 '37i9dQZF1DWSewYkkEomBp',
 '37i9dQZF1DWVLVzn60NyuA',
 '37i9dQZF1DWVAArCxuIRGQ',
 '37i9dQZF1DWSNsujEEbO9O',
 '37i9dQZF1DX9FIMhEujaK6',
 '37i9dQZF1DWZg863fGtALu',
 '37i9dQZF1DXaTitkvoNNxt',
 '37i9dQZF1DXcmybUHdi27L',
 '37i9dQZF1DXaS51xPOw5FD',
 '37i9dQZF1DXbIbVYph0Zr5',
 '37i9dQZF1DWTUoU0bd0p84',
 '37i9dQZF1DXbwoaqxaoAVr',
 '37i9dQZF1DWZ7eJRBxKzdO',
 '37i9dQZF1DWZSdcRHMl2tT',
 '37i9dQZF1DWY0BsMpCzERZ',
 

In [28]:
len(playlist_ids)

1985

In [122]:
def get_playlist_id():
    category_playlists = sp.category_playlists(category_id = category_id, country = 'GB')
    category_playlist_ids = []
    for item in category_playlists['playlists']['items']:
        category_playlist_ids.append(item['id'])
    return category_playlist_ids

In [123]:
category_playlist_ids = get_playlist_id()

In [125]:
category_playlist_ids

['37i9dQZF1DWY4lFlS4Pnso', '37i9dQZF1DXdc6Ams1C6tL', '37i9dQZF1DWW1yuCSjnKtM', '37i9dQZF1DX0s5kDXi1oC5', '37i9dQZF1DX1eh709zIoRH', '37i9dQZF1DX5uokaTN4FTR', '37i9dQZF1DX2L0iB23Enbq', '37i9dQZF1DWSVtp02hITpN', '37i9dQZF1DWVlYsZJXqdym', '37i9dQZF1DWVrBRunTOXCY', '37i9dQZF1DWSVtp02hITpN', '37i9dQZF1DWZjCOHYzGCXB', '37i9dQZF1DWVlYsZJXqdym', '37i9dQZF1DWXWBMhgr0bkX', '37i9dQZF1DWZ0Y50OtuhLO', '37i9dQZF1DXaiLfJ2acJnZ', '37i9dQZF1DWXetIPpoiRSb', '37i9dQZF1DX2czWA9hqErK', '37i9dQZF1DX4v0Y84QklHD', '37i9dQZF1DWX3xqQKu0Sgn']

In [29]:
playlist_tracks = sp.playlist_tracks(playlist_id)

In [124]:
len(category_playlist_ids)

20

In [30]:
pprint.pprint(playlist_tracks)

{'href': 'https://api.spotify.com/v1/playlists/37i9dQZF1DWY4lFlS4Pnso/tracks?offset=0&limit=100&additional_types=track',
 'items': [{'added_at': '2022-11-25T00:00:00Z',
            'added_by': {'external_urls': {'spotify': 'https://open.spotify.com/user/'},
                         'href': 'https://api.spotify.com/v1/users/',
                         'id': '',
                         'type': 'user',
                         'uri': 'spotify:user:'},
            'is_local': False,
            'primary_color': None,
            'track': {'album': {'album_type': 'single',
                                'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/1zNqDE7qDGCsyzJwohVaoX'},
                                             'href': 'https://api.spotify.com/v1/artists/1zNqDE7qDGCsyzJwohVaoX',
                                             'id': '1zNqDE7qDGCsyzJwohVaoX',
                                             'name': 'Anne-Marie',
                                 

                                            'ML',
                                            'MN',
                                            'MO',
                                            'MR',
                                            'MT',
                                            'MU',
                                            'MV',
                                            'MW',
                                            'MX',
                                            'MY',
                                            'MZ',
                                            'NA',
                                            'NE',
                                            'NG',
                                            'NI',
                                            'NL',
                                            'NO',
                                            'NP',
                                            'NR',
                                            'NZ',


                                            'url': 'https://i.scdn.co/image/ab67616d0000b273a3a7f38ea2033aa501afd4cf',
                                            'width': 640},
                                           {'height': 300,
                                            'url': 'https://i.scdn.co/image/ab67616d00001e02a3a7f38ea2033aa501afd4cf',
                                            'width': 300},
                                           {'height': 64,
                                            'url': 'https://i.scdn.co/image/ab67616d00004851a3a7f38ea2033aa501afd4cf',
                                            'width': 64}],
                                'name': 'Calm Down (with Selena Gomez)',
                                'release_date': '2022-08-25',
                                'release_date_precision': 'day',
                                'total_tracks': 1,
                                'type': 'album',
                                'uri': 'spotify:a

                                                      'MZ',
                                                      'NA',
                                                      'NE',
                                                      'NG',
                                                      'NI',
                                                      'NL',
                                                      'NO',
                                                      'NP',
                                                      'NR',
                                                      'OM',
                                                      'PA',
                                                      'PE',
                                                      'PG',
                                                      'PH',
                                                      'PK',
                                                      'PL',
                                        

                      'track_number': 1,
                      'type': 'track',
                      'uri': 'spotify:track:39JofJHEtg8I4fSyo7Imft'},
            'video_thumbnail': {'url': None}},
           {'added_at': '2022-11-25T00:00:00Z',
            'added_by': {'external_urls': {'spotify': 'https://open.spotify.com/user/'},
                         'href': 'https://api.spotify.com/v1/users/',
                         'id': '',
                         'type': 'user',
                         'uri': 'spotify:user:'},
            'is_local': False,
            'primary_color': None,
            'track': {'album': {'album_type': 'single',
                                'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/1nzgtKYFckznkcVMR3Gg4z'},
                                             'href': 'https://api.spotify.com/v1/artists/1nzgtKYFckznkcVMR3Gg4z',
                                             'id': '1nzgtKYFckznkcVMR3Gg4z',
                        

...

                                            'PA',
                                            'PE',
                                            'PG',
                                            'PH',
                                            'PK',
                                            'PL',
                                            'PS',
                                            'PT',
                                            'PW',
                                            'PY',
                                            'QA',
                                            'RO',
                                            'RS',
                                            'RW',
                                            'SA',
                                            'SB',
                                            'SC',
                                            'SE',
                                            'SG',
                                            'SI',


                                                      'GN',
                                                      'GQ',
                                                      'GR',
                                                      'GT',
                                                      'GW',
                                                      'GY',
                                                      'HK',
                                                      'HN',
                                                      'HR',
                                                      'HT',
                                                      'HU',
                                                      'ID',
                                                      'IE',
                                                      'IL',
                                                      'IN',
                                                      'IQ',
                                        

                                'release_date_precision': 'day',
                                'total_tracks': 1,
                                'type': 'album',
                                'uri': 'spotify:album:0GnxssqYa2RU9EdWHhZ707'},
                      'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/1Cs0zKBU1kc0i8ypK3B9ai'},
                                   'href': 'https://api.spotify.com/v1/artists/1Cs0zKBU1kc0i8ypK3B9ai',
                                   'id': '1Cs0zKBU1kc0i8ypK3B9ai',
                                   'name': 'David Guetta',
                                   'type': 'artist',
                                   'uri': 'spotify:artist:1Cs0zKBU1kc0i8ypK3B9ai'},
                                  {'external_urls': {'spotify': 'https://open.spotify.com/artist/4EPJlUEBy49EX1wuFOvtjK'},
                                   'href': 'https://api.spotify.com/v1/artists/4EPJlUEBy49EX1wuFOvtjK',
                                   'id

                                                      'LA',
                                                      'LB',
                                                      'LC',
                                                      'LI',
                                                      'LK',
                                                      'LR',
                                                      'LS',
                                                      'LT',
                                                      'LU',
                                                      'LV',
                                                      'LY',
                                                      'MA',
                                                      'MC',
                                                      'MD',
                                                      'ME',
                                                      'MG',
                                        

                                            'MK',
                                            'ML',
                                            'MN',
                                            'MO',
                                            'MR',
                                            'MT',
                                            'MU',
                                            'MV',
                                            'MW',
                                            'MX',
                                            'MY',
                                            'MZ',
                                            'NA',
                                            'NE',
                                            'NG',
                                            'NI',
                                            'NL',
                                            'NO',
                                            'NP',
                                            'NR',


In [31]:
pprint.pprint(playlist_tracks['items'])

[{'added_at': '2022-11-25T00:00:00Z',
  'added_by': {'external_urls': {'spotify': 'https://open.spotify.com/user/'},
               'href': 'https://api.spotify.com/v1/users/',
               'id': '',
               'type': 'user',
               'uri': 'spotify:user:'},
  'is_local': False,
  'primary_color': None,
  'track': {'album': {'album_type': 'single',
                      'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/1zNqDE7qDGCsyzJwohVaoX'},
                                   'href': 'https://api.spotify.com/v1/artists/1zNqDE7qDGCsyzJwohVaoX',
                                   'id': '1zNqDE7qDGCsyzJwohVaoX',
                                   'name': 'Anne-Marie',
                                   'type': 'artist',
                                   'uri': 'spotify:artist:1zNqDE7qDGCsyzJwohVaoX'},
                                  {'external_urls': {'spotify': 'https://open.spotify.com/artist/2PJEagPIxaBugeMjIyKVXF'},
                        

                                  'FM',
                                  'FR',
                                  'GA',
                                  'GB',
                                  'GD',
                                  'GE',
                                  'GH',
                                  'GM',
                                  'GN',
                                  'GQ',
                                  'GR',
                                  'GT',
                                  'GW',
                                  'GY',
                                  'HK',
                                  'HN',
                                  'HR',
                                  'HT',
                                  'HU',
                                  'ID',
                                  'IE',
                                  'IL',
                                  'IN',
                                  'IQ',
                                  'IS',


                                            'WS',
                                            'XK',
                                            'ZA',
                                            'ZM',
                                            'ZW'],
                      'external_urls': {'spotify': 'https://open.spotify.com/album/2b2GHWESCWEuHiCZ2Skedp'},
                      'href': 'https://api.spotify.com/v1/albums/2b2GHWESCWEuHiCZ2Skedp',
                      'id': '2b2GHWESCWEuHiCZ2Skedp',
                      'images': [{'height': 640,
                                  'url': 'https://i.scdn.co/image/ab67616d0000b273a3a7f38ea2033aa501afd4cf',
                                  'width': 640},
                                 {'height': 300,
                                  'url': 'https://i.scdn.co/image/ab67616d00001e02a3a7f38ea2033aa501afd4cf',
                                  'width': 300},
                                 {'height': 64,
                                  

                                            'GN',
                                            'GQ',
                                            'GR',
                                            'GT',
                                            'GW',
                                            'GY',
                                            'HK',
                                            'HN',
                                            'HR',
                                            'HT',
                                            'HU',
                                            'ID',
                                            'IE',
                                            'IL',
                                            'IN',
                                            'IQ',
                                            'IS',
                                            'IT',
                                            'JM',
                                            'JO',


                                  'SB',
                                  'SC',
                                  'SE',
                                  'SG',
                                  'SI',
                                  'SK',
                                  'SL',
                                  'SM',
                                  'SN',
                                  'SR',
                                  'ST',
                                  'SV',
                                  'SZ',
                                  'TD',
                                  'TG',
                                  'TH',
                                  'TJ',
                                  'TL',
                                  'TN',
                                  'TO',
                                  'TR',
                                  'TT',
                                  'TV',
                                  'TW',
                                  'TZ',


...

                                  'TN',
                                  'TO',
                                  'TR',
                                  'TT',
                                  'TV',
                                  'TW',
                                  'TZ',
                                  'UA',
                                  'UG',
                                  'US',
                                  'UY',
                                  'UZ',
                                  'VC',
                                  'VE',
                                  'VN',
                                  'VU',
                                  'WS',
                                  'XK',
                                  'ZA',
                                  'ZM',
                                  'ZW'],
            'disc_number': 1,
            'duration_ms': 170501,
            'episode': False,
            'explicit': True,
            'external_ids': {'isrc

                                  'KH',
                                  'KI',
                                  'KM',
                                  'KN',
                                  'KR',
                                  'KW',
                                  'KZ',
                                  'LA',
                                  'LB',
                                  'LC',
                                  'LI',
                                  'LK',
                                  'LR',
                                  'LS',
                                  'LT',
                                  'LU',
                                  'LV',
                                  'LY',
                                  'MA',
                                  'MC',
                                  'MD',
                                  'ME',
                                  'MG',
                                  'MH',
                                  'MK',


                                  'IQ',
                                  'IS',
                                  'IT',
                                  'JM',
                                  'JO',
                                  'JP',
                                  'KE',
                                  'KG',
                                  'KH',
                                  'KI',
                                  'KM',
                                  'KN',
                                  'KR',
                                  'KW',
                                  'KZ',
                                  'LA',
                                  'LB',
                                  'LC',
                                  'LI',
                                  'LK',
                                  'LR',
                                  'LS',
                                  'LT',
                                  'LU',
                                  'LV',


                                            'UZ',
                                            'VC',
                                            'VE',
                                            'VN',
                                            'VU',
                                            'WS',
                                            'XK',
                                            'ZA',
                                            'ZM',
                                            'ZW'],
                      'external_urls': {'spotify': 'https://open.spotify.com/album/60qboewMs8i1L2a0fEGcVl'},
                      'href': 'https://api.spotify.com/v1/albums/60qboewMs8i1L2a0fEGcVl',
                      'id': '60qboewMs8i1L2a0fEGcVl',
                      'images': [{'height': 640,
                                  'url': 'https://i.scdn.co/image/ab67616d0000b27347e6082946ca0508c9d31f80',
                                  'width': 640},
                                 {'heig

                                            'LU',
                                            'LV',
                                            'LY',
                                            'MA',
                                            'MC',
                                            'MD',
                                            'ME',
                                            'MG',
                                            'MH',
                                            'MK',
                                            'ML',
                                            'MN',
                                            'MO',
                                            'MR',
                                            'MT',
                                            'MU',
                                            'MV',
                                            'MW',
                                            'MX',
                                            'MY',


In [179]:
def get_playlists_tracks(playlist_ids):
    track_ids = []
    for item in playlist_ids:
        playlist_tracks = sp.playlist_tracks(item)
        for i in playlist_tracks['items']:
            try:
                track_ids.append(i['track']['id']) 
            except:
                continue
    return track_ids 

In [180]:
track_ids = get_playlists_tracks(playlist_ids)

In [181]:
len(track_ids)

148433

In [1]:
import pickle

In [184]:
# with open ('tracks_GB.pkl', 'wb') as f:
#     pickle.dump(track_ids,f)

In [3]:
with open ('tracks_GB.pkl', 'rb') as f:
    track_ids = pickle.load(f)

In [19]:
len(track_ids)

148433

In [24]:
def extract_features2(track_ids):
    list_of_audio_features = []
    for item in track_ids:
        try:
            list_of_audio_features.append(sp.audio_features(item)[0])
        except: 
            continue
    return list_of_audio_features

In [25]:
audio_features2 = extract_features2(track_ids)

In [45]:
type(audio_features2)

list

In [46]:
audio_features2[0]

{'danceability': 0.62,
 'energy': 0.681,
 'key': 9,
 'loudness': -4.915,
 'mode': 1,
 'speechiness': 0.356,
 'acousticness': 0.0138,
 'instrumentalness': 0,
 'liveness': 0.0248,
 'valence': 0.741,
 'tempo': 160.743,
 'type': 'audio_features',
 'id': '1eprzC29mwUQqcVj0eILdx',
 'uri': 'spotify:track:1eprzC29mwUQqcVj0eILdx',
 'track_href': 'https://api.spotify.com/v1/tracks/1eprzC29mwUQqcVj0eILdx',
 'analysis_url': 'https://api.spotify.com/v1/audio-analysis/1eprzC29mwUQqcVj0eILdx',
 'duration_ms': 162493,
 'time_signature': 4}

In [53]:
cleaned_list = []
for item in audio_features2 :
    if item is None:
        continue
    else:
        cleaned_list.append(item)

In [56]:
spotify_tracks_df = pd.DataFrame(cleaned_list)
spotify_tracks_df=spotify_tracks_df[["danceability","energy","loudness","speechiness","acousticness",
    "instrumentalness","liveness","valence","tempo","id","duration_ms"]]

spotify_tracks_df

danceability  energy  loudness  speechiness  acousticness  \
0              0.620   0.681    -4.915       0.3560        0.0138   
1              0.807   0.376    -7.768       0.0638        0.3790   
2              0.838   0.525    -3.562       0.0665        0.3450   
3              0.620   0.837    -4.356       0.1300        0.1280   
4              0.637   0.643    -6.571       0.0519        0.1300   
...              ...     ...       ...          ...           ...   
148063         0.806   0.706    -6.044       0.0909        0.0280   
148064         0.511   0.821    -6.459       0.0706        0.1590   
148065         0.719   0.547   -13.190       0.0362        0.0679   
148066         0.907   0.917    -5.464       0.0778        0.1200   
148067         0.658   0.748    -6.159       0.0353        0.2040   

        instrumentalness  liveness  valence    tempo                      id  \
0               0.000000    0.0248    0.741  160.743  1eprzC29mwUQqcVj0eILdx   
1               0.003870    0.1140    0.671  104.908  7cFPWLFiE60sdgzPsyydUJ   
2               0.000002    0.0771    0.884  144.981  0QHEIqNKsMoOY5urbzN48u   
3               0.000242    0.2420    0.433  172.081  5RobAV5ROH5KARimi7n3cO   
4               0.000002    0.1420    0.533   97.008  0V3wPSX9ygBnCm8psDIegu   
...                  ...       ...      ...      ...                     ...   
148063          0.000000    0.0700    0.608  112.985  1tJtx09XQnxaynZLOaTNfZ   
148064          0.000000    0.1220    0.630  121.074  1ygacgsmdK4Y1WQcJuZQHb   
148065          0.000003    0.2290    0.554  121.724  1ip1ULxxvAzaqH3VqKObdu   
148066          0.047500    0.0390    0.906  108.210  76as3dkOkHGMAvwmaKXPMD   
148067          0.000006    0.1380    0.662  129.030  5CGziaEatzKez145qf7Xj2   

        duration_ms  
0            162493  
1            209291  
2            134256  
3            170438  
4            200690  
...             ...  
148063       312355  
148064       215067  
148065       316000  
148066       246240  
148067       229213  

[148068 rows x 11 columns]

In [58]:
spotify_final_tracks_df = pd.concat([spotify_tracks_df,tracks_df], ignore_index=True)

NameError: name 'tracks_df' is not defined

In [62]:
spotify_tracks_df.to_csv('spotify_tracks_df.csv',index = False) 